<a href="https://colab.research.google.com/github/yuliiabosher/Map/blob/main/Map.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [6]:
!pip install geopandas
!pip install pyogrio

In [7]:
import geopandas as gpd
import pandas as pd
import pyogrio
import folium

In [8]:
def read_shape_file(file, object_type):
  district = gpd.read_file(file, engine="pyogrio", columns=['name','type', 'geometry'], where=f"type='{object_type}'", layer=0)
  return district

In [9]:
file_list = ["https://download.geofabrik.de/russia/central-fed-district-latest-free.shp.zip", "https://download.geofabrik.de/russia/crimean-fed-district-latest-free.shp.zip", \
"https://download.geofabrik.de/russia/far-eastern-fed-district-latest-free.shp.zip", "https://download.geofabrik.de/russia/north-caucasus-fed-district-latest-free.shp.zip", \
"https://download.geofabrik.de/russia/northwestern-fed-district-latest-free.shp.zip", "https://download.geofabrik.de/russia/siberian-fed-district-latest-free.shp.zip", \
"https://download.geofabrik.de/russia/south-fed-district-latest-free.shp.zip", "https://download.geofabrik.de/russia/ural-fed-district-latest-free.shp.zip", \
"https://download.geofabrik.de/russia/volga-fed-district-latest-free.shp.zip", "https://download.geofabrik.de/russia/kaliningrad-latest-free.shp.zip"]

In [12]:
def concatenate_dfs(list_of_files, type_of_object):
  list_of_dfs = []
  for i in list_of_files:
    list_of_dfs.append(read_shape_file(i, type_of_object))
  df = pd.concat(list_of_dfs)
  return df
ship_df = concatenate_dfs(file_list, "ship")

In [14]:
def display_map():
  street_map = folium.Map(location = [47.233334, 39.700001], zoom_start=4)
  return street_map
background_map = display_map()
display(background_map)

In [17]:
def display_popups(popup_df, bg_map):
  folium.GeoJson(popup_df.geometry).add_to(bg_map)
  popup_df['center'] = [x.geometry.centroid for i, x in popup_df.iterrows()]
  popup_df['location'] = [(row.center.y, row.center.x) for index, row in popup_df.iterrows()]
  for index, row in popup_df.iterrows():
    location = [row['location'][0], row['location'][1]]
    popup = f"<strong>{row['name']}</strong>"
    marker = folium.Marker(location=location, popup=popup)
    marker.add_to(bg_map)
  return bg_map
add_ship_markers = display_popups(ship_df, background_map)
display(add_ship_markers)

In [18]:
military_df = concatenate_dfs(file_list, "military")
add_military_markers = display_popups(military_df, background_map)
display(add_military_markers)